<a href="https://colab.research.google.com/github/Tomiinek/Multilingual_Text_to_Speech/blob/master/notebooks/code_switching_demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Multilingual Text-to-Speech Demo

This notebook demonstrates multilingual code-switching text-to-speech using:

- Tacotron based spectrogram generation: https://github.com/Tomiinek/Multilingual_Text_to_Speech
- WaveRNN vocoder: https://github.com/Tomiinek/WaveRNN, forked from fatchord/WaveRNN


**Estimated time to complete**: 5 minutes



In [1]:
import IPython
from IPython.display import Audio

In [2]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "7"
import sys
sys.path.append('../')
from utils.text import _phonemize,_phonemize_zh,to_pinyin,convert_kanji,create_manifest
from utils.multilingual_text import gen_mul_manifest
from utils.audio import change_frame_rate
import os
import soundfile as sf

/opt/conda/lib/python3.6/site-packages/numba/errors.py:105: UserWarning: Insufficiently recent colorama version found. Numba requires colorama >= 0.3.9
  warnings.warn(msg)


## Clone repositories

## Download pre-trained models

## Install dependencies

## Input texts to be synthesized

Inputs consist of **three parts delimited** by `|`:
  - **Input utterance** - Only a basic normalization is applied to input utterances, so **you should not use obscure characters and punctuation**. See the examples below that are formatted properly.
  - **Speaker ID** - There are more available speaker IDs, but **you should use just one of** `00-fr`, `00-de`, `00-nl`, `09-ru`, and `00-zh` as the WaveRNN vocoder was trained only on their voices.
  - **Per-character language** specification - You have to provide a **list of language codes** (one of `de`, `fr`, `nl`, `ru`, `zh`) **with the number of their characters delimited by comma**, e.g., `l1-n1,l2-n2,l3` says that the language `l1` occupies `n1` characters from the beginning, the language `l2` takes next `n2` characters and the language `l3` has all the remaining characters to the end. **You can mix up more languages** to control accent by replacing language codes (such as `l1`) with `l1*w1:l2*w2`, which means that the language `l1` has the weight `w1` and `l2` has the weight `w2`. For example, `de*0.75:fr*0.25` combines German and French with more emphasis on German.

Feel free to modify the examples below.






**Run this to demonstrate code switching:**

In [3]:
inputs = [
    "Cette requête s'explique par les relations peu conventionnelles que Schrödinger entretient avec les femmes:|00-fr|fr-68,de-11,fr",
    "Ces quartiers, parmi lesquels figurent De Pijp, le Kinkerbuurt et le Dapperbuurt, sont principalement financés par des banquiers et|00-fr|fr-39,nl-7,fr-5,nl-11,fr-7,nl-11,fr",
    "Les romans de Фёдор Михайлович Достоевский sont parfois qualifiés de métaphysiques,|00-fr|fr-14,ru-28,fr",
    "Le yǒngdìnghé est une rivière du nord de la Chine. Elle est l'un des tributaires du fleuve hǎihé.|00-fr|fr-3,zh-10,fr-78,zh-5,fr",
    "François Hollande ist ein französischer Politiker der Sozialistischen Partei und war Staatspräsident der Französischen Republik.|00-de|fr-17,de",
    "Sie liegt zwischen dem Ijsselmeer, der Ijssel und den Hügeln der Veluwe.|00-de|de-23,nl-10,de-6,nl-6,de-20,nl",
    "Ключевская сопка erreicht ihre außerordentliche Höhe,|00-de|ru-16,de",
    "Der tiānān ménguǎngcháng ist ein Platz im Zentrum von Peking, der Hauptstadt der Volksrepublik China.|00-de|de-4,zh-20,de",
    "Als men langs deze laan loopt van de Brandenburger Tor tot aan de Alexanderplatz over de Schloßbrücke vanaf welke|00-nl|nl-37,de-17,nl-12,de-14,nl-9,de-12,nl",
    "De naam van De Gaulle leeft voort in het grootste vliegveld van Frankrijk, Aéroport Charles De Gaulle.|00-nl|nl-12,fr-9,nl-54,fr-26,nl",
    "Nog steeds wordt Александр Сергеевич Пушкин in de Russische wereld en daarbuiten vereerd en gelezen.|00-nl|nl-17,ru-26,nl",
    "De chángjiāng stroomt vervolgens door zhòngqìng, de grootste stad van sìchuān.|00-nl|nl-3,zh-10,nl-25,zh-9,nl-23,zh-7,nl",
    "При нём трудами Pöppelmanna и других придворных мастеров центр Dresdenа приобрёл знакомый облик в стиле барокко.|09-ru|ru-16,de-10,ru-37,de-7,ru",
    "Как считают современные археологи, на месте Notre-Dame de Paris находились четыре различных храма:|09-ru|ru-44,fr-19,ru",
    "Johannes Vermeer van Delft был известным экспертом по вопросам искусства.|09-ru|nl-26,ru",
    "На протяжении истории běijīng был известен в Китае под разными именами.|09-ru|ru-22,zh-7,ru",
    "tā de fùqīn Rudolf Schrödinger è shì shēngchǎn yóubù hé fángshǔibù de gōngchǎng zhǔ tóngshí yě shì yīmíng yuányìjiā。|00-zh|zh-12,de-18,zh",
    "tāmen tóupiào juédìng jiànzào Sacré-Coeur， érqiě dìngyìtā wèi dùi bālígōngshè shèyuán suǒ fànxià de zùixíng de bǔcháng|00-zh|zh-30,fr-11,zh",
    "Vincent van Gogh de wǔwèi bóbó shūshū men， yǒu sānwèi shì xiāngdāng chénggōng de yìshùpǐn jiāoyìshāng。|00-zh|nl-16,zh",
    "yóuyú Александр shì dùi Кутузов huáiyǒu ègǎn， tā zài jūndùi de lǐngdǎozhíwù bèi zàicì chèxiāo。|00-zh|zh-6,ru-9,zh-9,ru-7,zh"
]

**Run this to demonstrate smooth pronunciation control:**

In [4]:
inputs = [
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|fr",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.1:fr*0.9",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.2:fr*0.8",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.3:fr*0.7",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.4:fr*0.6",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.5:fr*0.5",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.6:fr*0.4",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.7:fr*0.3",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.8:fr*0.2",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de*0.9:fr*0.1",
    "Jean-Paul Marat fait deux voyages en Angleterre au temps de la Révolution.|00-fr|de",
]

**Run this to demonstrate voice cloning:**

In [34]:
inputs = [
    "Der Distrikt liegt in den Kafueauen und ist von Landwirtschaft geprägt.|00-fr|de",
    "Der Distrikt liegt in den Kafueauen und ist von Landwirtschaft geprägt.|00-de|de",
    "Le texte complet de l'initiative peut être consulté sur le site de la Chancellerie fédérale.|00-fr|fr",
    "Le texte complet de l'initiative peut être consulté sur le site de la Chancellerie fédérale.|00-de|fr",
#     "Dit wordt de start van Van Oostzanens carrière als zelfstandig kunstschilder.|00-fr|nl",
#     "Dit wordt de start van Van Oostzanens carrière als zelfstandig kunstschilder.|00-de|nl",
    "Название штата произошло благодаря серии картографических ошибок и неточностей.|00-fr|ru",
    "Название штата произошло благодаря серии картографических ошибок и неточностей.|00-de|ru",
    "jìsuànjī dàxué zhǔyào xuékē shì kēxué hé jìzhúbù， xuéshēng kěyǐ huòqǔ jìsuànjīkēxué hé jìzhú de běnkē xuéwèi|00-fr|zh",
    "jìsuànjī dàxué zhǔyào xuékē shì kēxué hé jìzhúbù， xuéshēng kěyǐ huòqǔ jìsuànjīkēxué hé jìzhú de běnkē xuéwèi|00-de|zh"
]

### 不同人说de、fr、nl、ru

In [9]:
text_de = '100 Der Distrikt liegt in den Kafueauen und ist von Landwirtschaft geprägt.'
text_fr = "Le texte complet de l'initiative peut être consulté sur le site de la Chancellerie fédérale."
text_nl = "Dit wordt de start van Van Oostzanens carrière als zelfstandig kunstschilder."
text_ru ="Название штата произошло благодаря серии картографических ошибок и неточностей."
ipa_text = _phonemize(text_de,'de')
ipa_text2 = _phonemize(text_fr,'fr-fr')
ipa_text3 = _phonemize(text_nl,'nl')
ipa_text4 = _phonemize(text_ru,'ru')

print(ipa_text)
print(ipa_text2)
print(ipa_text3)
print(ipa_text4)


aɪnhʊndɜt dɛɾ dɪstɾɪkt liːkt ɪn deːn kɑfuːeːaʊən ʊnt ɪst fɔn lantvɪɾtʃaft ɡəpɾɛːkt .
lə tɛkst kɔ̃plɛ də linisjativ pøt ɛtʁ kɔ̃sylte syʁ lə sit də la ʃɑ̃sɛlʁi fedeʁal .
dɪt ʋɔr tə stɑrt vɑn vɑn oːstzaːnəns kɑɾriɛrə ɑl sɛlfstɑndəx kɵnstsxɪldər .
nazvɑnijɪ ʃtɑta prʌizʌʃɭo bɭʌɡʌdarʲɑ sʲerʲiɪ kʌrtʌɡrafʲitʃʲiskʲix ʌʃybʌk i nitotʃʲnʌsʲtʲij .


In [ ]:
speaker_list=['lance-zh','hotpot-zh','00-zh','00-en','EPwchina','00-de']
inputs = []
for speaker in speaker_list:
    inputs.append(f"{ipa_text1}|{speaker}|de")
    inputs.append(f"{ipa_text2}|{speaker}|fr")
 

In [159]:
inputs = [
    "dɛɾ dɪstɾɪkt liːkt ɪn deːn kɑfuːeːaʊən ʊnt ɪst fɔn lantvɪɾtʃaft ɡəpɾɛːkt .|00-en|de",
    "dɛɾ dɪstɾɪkt liːkt ɪn deːn kɑfuːeːaʊən ʊnt ɪst fɔn lantvɪɾtʃaft ɡəpɾɛːkt .|00-de|de",
    "dɛɾ dɪstɾɪkt liːkt ɪn deːn kɑfuːeːaʊən ʊnt ɪst fɔn lantvɪɾtʃaft ɡəpɾɛːkt .|lance-zh|de",

    "lə tɛkst kɔ̃plɛ də linisjativ pøt ɛtʁ kɔ̃sylte syʁ lə sit də la ʃɑ̃sɛlʁi fedeʁal .|00-en|fr",
    "lə tɛkst kɔ̃plɛ də linisjativ pøt ɛtʁ kɔ̃sylte syʁ lə sit də la ʃɑ̃sɛlʁi fedeʁal .|00-de|fr",
    "lə tɛkst kɔ̃plɛ də linisjativ pøt ɛtʁ kɔ̃sylte syʁ lə sit də la ʃɑ̃sɛlʁi fedeʁal .|lance-zh|fr",

#     "dɪt ʋɔr tə stɑrt vɑn vɑn oːstzaːnəns kɑɾriɛrə ɑl sɛlfstɑndəx kɵnstsxɪldər .|00-fr|nl",
#     "dɪt ʋɔr tə stɑrt vɑn vɑn oːstzaːnəns kɑɾriɛrə ɑl sɛlfstɑndəx kɵnstsxɪldər .|00-de|nl",
    "nazvɑnijɪ ʃtɑta prʌizʌʃɭo bɭʌɡʌdarʲɑ sʲerʲiɪ kʌrtʌɡrafʲitʃʲiskʲix ʌʃybʌk i nitotʃʲnʌsʲtʲij .|00-en|ru",
    "nazvɑnijɪ ʃtɑta prʌizʌʃɭo bɭʌɡʌdarʲɑ sʲerʲiɪ kʌrtʌɡrafʲitʃʲiskʲix ʌʃybʌk i nitotʃʲnʌsʲtʲij .|00-de|ru",
    "nazvɑnijɪ ʃtɑta prʌizʌʃɭo bɭʌɡʌdarʲɑ sʲerʲiɪ kʌrtʌɡrafʲitʃʲiskʲix ʌʃybʌk i nitotʃʲnʌsʲtʲij .|cary-zh|ru",

    
]

### 不同人说中文

In [5]:
print(_phonemize('1 2 3 4 5','cmn'))
print(_phonemize('一二三四五','cmn'))
print(_phonemize('yi1 er4 san1 si4 wu3 ','cmn'))
print(_phonemize('yi er san si wu，wu ji','cmn'))
print(_phonemize('yī èr sān sì wǔ，wū jī','cmn'))

ji5 ər5 sa5n si̪5 wu2
jiji5 ərsi̪5 sɑnji5 si̪si̪5 wusa5n
ji ji5 ər si̪5 sɑn ji5 si̪ si̪5 wu sa5n
ji ər sɑn si̪ wu ，wu tɕi
ji ji5 ərɜ sɑ ə5n si̪ wu ，wu tɕi


In [10]:
texts = ['大家好，我是清华珠三角研究院虚拟人物伊娃，很高兴认识大家，潮汕机场启用国内航班一证通关，我是汕头电视台主持人肖迪，十四是十四，四十是四十。']
pinyin_text = [to_pinyin(i, style='Style.TONE3') for i in texts]
# 原来中文预处理流程为：汉字转音素；目前新流程为汉字转拼音再转带音调的音素
ipa_texts = [_phonemize_zh(i) for i in texts]
# a=list(ipa_texts[-1])
# a[-5]='1'
# ipa_texts[-1]=''.join(a)
print(ipa_texts)

['tɑ4 tɕiɑ1 xɑu3 ， wo3 s.i.4 tɕhiŋ1 xwɑ2 ts.u1 sɑn1 tɕjɑu3 jiɑn2 tɕiou1 yɑn4 ɕy1 ni3 ʐon2 wu4 ji1 wɑ2 ， xon3 kɑu1 ɕiŋ4 ʐon4 s.i. tɑ4 tɕiɑ1 ， ts.hɑu2 s.ɑn4 tɕi1 ts.hɑŋ3 tɕhi3 jonɡ4 kuo2 nei4 xɑŋ2 pɑn1 ji1 ts.oŋ4 thonɡ1 kwɑn1 ， wo3 s.i.4 s.ɑn4 thou2 tiɑn4 s.i.4 thai2 ts.u3 ts.hi.2 ʐon2 ɕjɑu4 ti2 ， s.i.2 si̪4 s.i.4 s.i.2 si̪4 ， si̪4 s.i.2 s.i.4 si̪4 s.i.2 。']


In [11]:
speaker_list=['ShantouTV_xiaodi']
inputs = []
for ipa_text in ipa_texts:
    for speaker in speaker_list:
        inputs.append(f"{ipa_text}|{speaker}|zh")  
#         break
print(inputs)

['tɑ4 tɕiɑ1 xɑu3 ， wo3 s.i.4 tɕhiŋ1 xwɑ2 ts.u1 sɑn1 tɕjɑu3 jiɑn2 tɕiou1 yɑn4 ɕy1 ni3 ʐon2 wu4 ji1 wɑ2 ， xon3 kɑu1 ɕiŋ4 ʐon4 s.i. tɑ4 tɕiɑ1 ， ts.hɑu2 s.ɑn4 tɕi1 ts.hɑŋ3 tɕhi3 jonɡ4 kuo2 nei4 xɑŋ2 pɑn1 ji1 ts.oŋ4 thonɡ1 kwɑn1 ， wo3 s.i.4 s.ɑn4 thou2 tiɑn4 s.i.4 thai2 ts.u3 ts.hi.2 ʐon2 ɕjɑu4 ti2 ， s.i.2 si̪4 s.i.4 s.i.2 si̪4 ， si̪4 s.i.2 s.i.4 si̪4 s.i.2 。|ShantouTV_xiaodi|zh', 'tɑ4 tɕiɑ1 xɑu3 ， wo3 s.i.4 tɕhiŋ1 xwɑ2 ts.u1 sɑn1 tɕjɑu3 jiɑn2 tɕiou1 yɑn4 ɕy1 ni3 ʐon2 wu4 ji1 wɑ2 ， xon3 kɑu1 ɕiŋ4 ʐon4 s.i. tɑ4 tɕiɑ1 ， ts.hɑu2 s.ɑn4 tɕi1 ts.hɑŋ3 tɕhi3 jonɡ4 kuo2 nei4 xɑŋ2 pɑn1 ji1 ts.oŋ4 thonɡ1 kwɑn1 ， wo3 s.i.4 s.ɑn4 thou2 tiɑn4 s.i.4 thai2 ts.u3 ts.hi.2 ʐon2 ɕjɑu4 ti2 ， s.i.2 si̪4 s.i.4 s.i.2 si̪4 ， si̪4 s.i.2 s.i.4 si̪4 s.i.2 。|css10_zh|zh', 'tɑ4 tɕiɑ1 xɑu3 ， wo3 s.i.4 tɕhiŋ1 xwɑ2 ts.u1 sɑn1 tɕjɑu3 jiɑn2 tɕiou1 yɑn4 ɕy1 ni3 ʐon2 wu4 ji1 wɑ2 ， xon3 kɑu1 ɕiŋ4 ʐon4 s.i. tɑ4 tɕiɑ1 ， ts.hɑu2 s.ɑn4 tɕi1 ts.hɑŋ3 tɕhi3 jonɡ4 kuo2 nei4 xɑŋ2 pɑn1 ji1 ts.oŋ4 thonɡ1 kwɑn1 ， wo3 s.i.4 s.ɑn4 thou2 tiɑn

### 不同人说日文

In [3]:
texts = ['こんばんは。お会いできて嬉しいです。', '北京冬季五輪組織委員会は問題のガイドラインを堅持し、測定を尽くさなければならないという原則に基づき、完成した各種準備作業を全面的に点検した。']
ipa_texts = [convert_kanji(i) for i in texts]
ipa_texts = [_phonemize(i,'ja') for i in texts]
print(ipa_texts)

['ko̞ũbäũhä 。 o̞ äi de̞kite̞ ɯᵝɽe̞ɕi ide̞sɯᵝ 。', 'pe̞kiɴ to̞ɯᵝki ɡo̞ɽiɴ so̞ɕiki iːŋkäi hä mo̞ndäi no̞ɡäido̞ɽäiĩo̞ ke̞ũdʑi ɕi 、 so̞kɯᵝte̞i o̞ tsɯᵝkɯᵝsä näke̞ɽe̞bänäɽänäito̞iɯᵝ ɡe̞ũso̞kɯᵝ ni mo̞to̞zɯᵝ ki 、 käũse̞iɕi tä käkɯᵝɕɯᵝ dʑɯᵝũbisäɡʲo̞ɯᵝ o̞ ze̞mme̞nte̞ki ni te̞ŋke̞ɴ ɕitä 。']


In [10]:
speaker_list=['css10_ja']
inputs = []
for ipa_text in ipa_texts:
    for speaker in speaker_list:
        inputs.append(f"{ipa_text}|{speaker}|ja")        
print(inputs)

['ko̞ũbäũhä 。 o̞ äi de̞kite̞ ɯᵝɽe̞ɕi ide̞sɯᵝ 。|css10_ja|ja', 'pe̞kiɴ to̞ɯᵝki ɡo̞ɽiɴ so̞ɕiki iːŋkäi hä mo̞ndäi no̞ɡäido̞ɽäiĩo̞ ke̞ũdʑi ɕi 、 so̞kɯᵝte̞i o̞ tsɯᵝkɯᵝsä näke̞ɽe̞bänäɽänäito̞iɯᵝ ɡe̞ũso̞kɯᵝ ni mo̞to̞zɯᵝ ki 、 käũse̞iɕi tä käkɯᵝɕɯᵝ dʑɯᵝũbisäɡʲo̞ɯᵝ o̞ ze̞mme̞nte̞ki ni te̞ŋke̞ɴ ɕitä 。|css10_ja|ja']


### 不同人说英文

In [24]:
texts = ["Good evening. Nice to meet you.",
         "Network news, today April 10 is the countdown to the Beijing Winter Olympic Games 300 days, a 10-day Beijing Winter Olympic Games on the ice project test activities also came to an end today."]
ipa_texts = [_phonemize(i,'en-us') for i in texts]
print(ipa_texts)

['ɡʊd iːvnɪŋ . naɪs tə miːt juː .', 'nɛtwɜːk nuːz , tədeɪ eɪpɹəl tɛn ɪz ðə kaʊntdaʊn tə ðə beɪdʒɪŋ wɪntɚɹ əlɪmpɪk ɡeɪmz θɹiːhʌndɹəd deɪz , ɐ tɛndeɪ beɪdʒɪŋ wɪntɚɹ əlɪmpɪk ɡeɪmz ɔnðɪ aɪs pɹɑːdʒɛkt tɛst æktɪvɪɾiz ɔːlsoʊ keɪm tʊ ɐn ɛnd tədeɪ .']


In [18]:
speaker_list=['lj']
inputs = []
for ipa_text in ipa_texts:
    for speaker in speaker_list:
        inputs.append(f"{ipa_text}|{speaker}|en")        
print(inputs)

['ɡʊd iːvnɪŋ . naɪs tə miːt juː .|lj|en', 'ðə beɪdʒɪŋ ɔːɹɡənaɪzɪŋ kəmɪɾi fɚðə wɪntɚɹ əlɪmpɪk ɡeɪmz , ædhɪɹɪŋ tə ðə pɹɑːbləmoːɹiəntᵻd pɹɪnsɪpəl , kəndʌktᵻd ɐ kɑːmpɹihɛnsɪv ɪnspɛkʃən ʌv ɔːl ðə pɹɛpɚɹeɪʃənz ðæt hɐdbɪŋ kəmpliːɾᵻd ɪn ɐkoːɹdəns wɪððə pɹɪnsɪpəl ʌv ɔːl tɛsts ʃʊd biː dʌn|lj|en']


### 不同人说韩文

In [10]:
texts = ["cctv 소식 (뉴스련합방송):오늘 4월 10일이 북경동계올림픽 300일간의 카운트다운이고 10일간의 북경동계올림픽 빙상종목 시험활동도 오늘 막을 내렸다.",
         "북경동계올림픽조직위원회는 문제의 방향을 견지하여 마땅히 예측해야 하는 원칙에 따라 이미 완수된 제반 준비사업에 대해 전면적인 검사를 진행하였다."]
ipa_texts = [_phonemize(i,'ko') for i in texts]
print(ipa_texts)

[WARNING] 1 utterances containing language switches on lines 1
[WARNING] extra phones may appear in the "ko" phoneset
[WARNING] language switch flags have been removed (applying "remove-flags" policy)


['siːsiːtiːviː sosiqnjusɯɾjʌnhɐppɐŋsoŋ :onɯɫ sɐ wʌɫ sip iɾi puqkjʌŋdoŋqjeolimphiq sɐmpɛq iɫqɐnɯj khɐunthɯdɐuniqo sip iɫqɐnɯj puqkjʌŋdoŋqjeolimphiq piŋsɐŋdʑoŋmoq sihʌmhwɐɫdoŋdo onɯɫmɐqɯɫnɛɾjʌttɐ .', 'puqkjʌŋdoŋqjeolimphiqtɕodʑiqwiwʌnhwenɯnmundʑeɯj pɐŋhjɐŋɯɫ ɡjʌndʑihɐjʌmɐtɐŋhi jetʃhɯkhɛjɐ hɐnɯn wʌntʃhiqe tɐɾɐ imi wɐnsudwen tɕebɐn tɕunbisɐʌpe dɛhɛ tɕʌnmjʌndʑʌqin ɡʌmsɐɾɯɫ tɕinhɛŋhɐjʌttɐ .']


In [11]:
speaker_list=['kss']
inputs = []
for ipa_text in ipa_texts:
    for speaker in speaker_list:
        inputs.append(f"{ipa_text}|{speaker}|ko")        
print(inputs)


['siːsiːtiːviː sosiqnjusɯɾjʌnhɐppɐŋsoŋ :onɯɫ sɐ wʌɫ sip iɾi puqkjʌŋdoŋqjeolimphiq sɐmpɛq iɫqɐnɯj khɐunthɯdɐuniqo sip iɫqɐnɯj puqkjʌŋdoŋqjeolimphiq piŋsɐŋdʑoŋmoq sihʌmhwɐɫdoŋdo onɯɫmɐqɯɫnɛɾjʌttɐ .|kss|ko', 'puqkjʌŋdoŋqjeolimphiqtɕodʑiqwiwʌnhwenɯnmundʑeɯj pɐŋhjɐŋɯɫ ɡjʌndʑihɐjʌmɐtɐŋhi jetʃhɯkhɛjɐ hɐnɯn wʌntʃhiqe tɐɾɐ imi wɐnsudwen tɕebɐn tɕunbisɐʌpe dɛhɛ tɕʌnmjʌndʑʌqin ɡʌmsɐɾɯɫ tɕinhɛŋhɐjʌttɐ .|kss|ko']


### 不同人说混合语言

In [5]:
# "Ключевская сопка erreicht ihre außerordentliche Höhe,|00-de|ru-16,de"
s1="hello，我有十块人民币。python真好用"
# s2="Good to see you."
s3="Hello,“괜찮은”.こんばんは。1998年，お会いできて嬉しいです"
inputs,split_text,lang_text = gen_mul_manifest(s3,['Jingpin_Lance'])
inputs

['Hello,“', '괜찮은', '”', '.', 'こんばんは。', '1', '998', 'ねん，', 'おあいできてうれしいです'] ['en', 'ko', 'en', 'en', 'ja', 'en', 'en', 'ja', 'ja'] ['Jingpin_Lance']


['Hello,“괜찮은”.こんばんは。1998ねん，おあいできてうれしいです|Jingpin_Lance|en-7,ko-3,en-1,en-1,ja-6,en-1,en-3,ja-3,ja']

In [5]:
lang_text

['en', 'ko', 'ja']

## Synthesis

### Spectrogram and Waveform generation

In [21]:
# os.chdir(os.path.join(os.path.expanduser("~"), tacotron_dir))
if "utils" in sys.modules: del sys.modules["utils"]
if "../" in sys.path: sys.path.remove("../")
if "../WaveRNN" in sys.path: sys.path.remove("../WaveRNN")
sys.path.append("../")
from synthesize import synthesize
from utils import build_model

# 中英文 20210225_2lang_22k_loss-999-0.196 可用
# 韩语 20210318_ko_22k_loss-499-0.112 speaker：kss可用

chpt_path = "../checkpoints/20210225_2lang_22k_loss-999-0.196"

model = build_model(chpt_path)
model.eval()

if "utils" in sys.modules: del sys.modules["utils"]
if "../" in sys.path: sys.path.remove("../")
if "../WaveRNN" in sys.path: sys.path.remove("../WaveRNN")
sys.path.append("../WaveRNN")
from models.fatchord_version import WaveRNN
from utils import hparams as hp

from gen_wavernn import generate
import torch

hp.configure('../WaveRNN/hparams.py')
model_wavernn = WaveRNN(rnn_dims=hp.voc_rnn_dims, fc_dims=hp.voc_fc_dims, bits=hp.bits, pad=hp.voc_pad, upsample_factors=hp.voc_upsample_factors, 
                feat_dims=hp.num_mels, compute_dims=hp.voc_compute_dims, res_out_dims=hp.voc_res_out_dims, res_blocks=hp.voc_res_blocks, 
                hop_length=hp.hop_length, sample_rate=hp.sample_rate, mode=hp.voc_mode).to(torch.device('cuda' if torch.cuda.is_available() else 'cpu'))

wavernn_chpt = "wavernn_weight.pyt"
# wavernn_chpt = "wavernn_ShantouTV_1000k.pyt"
model_wavernn.load(os.path.join("../chpt", wavernn_chpt))

print("Loading model complete.")

Trainable Parameters: 4.744M
Loading model complete.


In [25]:
spectrograms = [synthesize(model, "|" + i) for i in inputs]
waveforms = [generate(model_wavernn, s, hp.voc_gen_batched, hp.voc_target, hp.voc_overlap) for s in spectrograms]

| ████████████████ 408000/411400 | Batch Size: 34 | Gen Rate: 24.5kHz | 

## Resulting audios



### 保存语音并生成manifest文件

In [23]:
i=1
output_dir = "/data/jerik/MTS_zhu/notebooks/output"
json_list=[]
if not os.path.exists(output_dir):
    os.mkdir(output_dir)
    
for waveform in waveforms:
    file_name = os.path.join(output_dir,'output_'+str(i)+'.wav')
    sf.write(file_name,data=waveform,samplerate=hp.sample_rate)
    display(Audio(file_name))
    json_list.append((create_manifest(texts[i-1],file_name)))
    i+=1
with open(os.path.join(output_dir,'manifest.test'), 'w',encoding='utf-8') as out_file:
    for line in json_list:
        out_file.write(line + '\n')

In [4]:
# 中文测评需要将语音采样率将至8k
import glob
file_list = glob.glob('./output/*.wav')
for file in file_list:
    change_frame_rate(file,8000)

### 中文

In [20]:
for idx, w in enumerate(waveforms):
    print(inputs[idx])
    IPython.display.display(IPython.display.Audio(data=w, rate=hp.sample_rate))

tɑ4 tɕiɑ1 xɑu3 ， wo3 s.i.4 tɕhiŋ1 xwɑ2 ts.u1 sɑn1 tɕjɑu3 jiɑn2 tɕiou1 yɑn4 ɕy1 ni3 ʐon2 wu4 ji1 wɑ2 ， xon3 kɑu1 ɕiŋ4 ʐon4 s.i. tɑ4 tɕiɑ1 ， ts.hɑu2 s.ɑn4 tɕi1 ts.hɑŋ3 tɕhi3 jonɡ4 kuo2 nei4 xɑŋ2 pɑn1 ji1 ts.oŋ4 thonɡ1 kwɑn1 ， wo3 s.i.4 s.ɑn4 thou2 tiɑn4 s.i.4 thai2 ts.u3 ts.hi.2 ʐon2 ɕjɑu4 ti2 ， s.i.2 si̪4 s.i.4 s.i.2 si̪4 ， si̪4 s.i.2 s.i.4 si̪4 s.i.2 。|ShantouTV_xiaodi|zh


tɑ4 tɕiɑ1 xɑu3 ， wo3 s.i.4 tɕhiŋ1 xwɑ2 ts.u1 sɑn1 tɕjɑu3 jiɑn2 tɕiou1 yɑn4 ɕy1 ni3 ʐon2 wu4 ji1 wɑ2 ， xon3 kɑu1 ɕiŋ4 ʐon4 s.i. tɑ4 tɕiɑ1 ， ts.hɑu2 s.ɑn4 tɕi1 ts.hɑŋ3 tɕhi3 jonɡ4 kuo2 nei4 xɑŋ2 pɑn1 ji1 ts.oŋ4 thonɡ1 kwɑn1 ， wo3 s.i.4 s.ɑn4 thou2 tiɑn4 s.i.4 thai2 ts.u3 ts.hi.2 ʐon2 ɕjɑu4 ti2 ， s.i.2 si̪4 s.i.4 s.i.2 si̪4 ， si̪4 s.i.2 s.i.4 si̪4 s.i.2 。|css10_zh|zh


tɑ4 tɕiɑ1 xɑu3 ， wo3 s.i.4 tɕhiŋ1 xwɑ2 ts.u1 sɑn1 tɕjɑu3 jiɑn2 tɕiou1 yɑn4 ɕy1 ni3 ʐon2 wu4 ji1 wɑ2 ， xon3 kɑu1 ɕiŋ4 ʐon4 s.i. tɑ4 tɕiɑ1 ， ts.hɑu2 s.ɑn4 tɕi1 ts.hɑŋ3 tɕhi3 jonɡ4 kuo2 nei4 xɑŋ2 pɑn1 ji1 ts.oŋ4 thonɡ1 kwɑn1 ， wo3 s.i.4 s.ɑn4 thou2 tiɑn4 s.i.4 thai2 ts.u3 ts.hi.2 ʐon2 ɕjɑu4 ti2 ， s.i.2 si̪4 s.i.4 s.i.2 si̪4 ， si̪4 s.i.2 s.i.4 si̪4 s.i.2 。|Jingpin_Lance|zh


### 日文

In [12]:
for idx, w in enumerate(waveforms):
    print(inputs[idx])
    IPython.display.display(IPython.display.Audio(data=w, rate=hp.sample_rate))

ko̞ũbäũhä 。 o̞ äi de̞kite̞ ɯᵝɽe̞ɕi ide̞sɯᵝ 。|css10_ja|ja


pe̞kiɴ to̞ɯᵝki ɡo̞ɽiɴ so̞ɕiki iːŋkäi hä mo̞ndäi no̞ɡäido̞ɽäiĩo̞ ke̞ũdʑi ɕi 、 so̞kɯᵝte̞i o̞ tsɯᵝkɯᵝsä näke̞ɽe̞bänäɽänäito̞iɯᵝ ɡe̞ũso̞kɯᵝ ni mo̞to̞zɯᵝ ki 、 käũse̞iɕi tä käkɯᵝɕɯᵝ dʑɯᵝũbisäɡʲo̞ɯᵝ o̞ ze̞mme̞nte̞ki ni te̞ŋke̞ɴ ɕitä 。|css10_ja|ja


### 英文

In [26]:
for idx, w in enumerate(waveforms):
    print(inputs[idx])
    IPython.display.display(IPython.display.Audio(data=w, rate=hp.sample_rate))

ɡʊd iːvnɪŋ . naɪs tə miːt juː .|lj|en


ðə beɪdʒɪŋ ɔːɹɡənaɪzɪŋ kəmɪɾi fɚðə wɪntɚɹ əlɪmpɪk ɡeɪmz , ædhɪɹɪŋ tə ðə pɹɑːbləmoːɹiəntᵻd pɹɪnsɪpəl , kəndʌktᵻd ɐ kɑːmpɹihɛnsɪv ɪnspɛkʃən ʌv ɔːl ðə pɹɛpɚɹeɪʃənz ðæt hɐdbɪŋ kəmpliːɾᵻd ɪn ɐkoːɹdəns wɪððə pɹɪnsɪpəl ʌv ɔːl tɛsts ʃʊd biː dʌn|lj|en


### 其他

In [13]:
for idx, w in enumerate(waveforms):
    print(inputs[idx])
    IPython.display.display(IPython.display.Audio(data=w, rate=hp.sample_rate))

siːsiːtiːviː sosiqnjusɯɾjʌnhɐppɐŋsoŋ :onɯɫ sɐ wʌɫ sip iɾi puqkjʌŋdoŋqjeolimphiq sɐmpɛq iɫqɐnɯj khɐunthɯdɐuniqo sip iɫqɐnɯj puqkjʌŋdoŋqjeolimphiq piŋsɐŋdʑoŋmoq sihʌmhwɐɫdoŋdo onɯɫmɐqɯɫnɛɾjʌttɐ .|kss|ko


puqkjʌŋdoŋqjeolimphiqtɕodʑiqwiwʌnhwenɯnmundʑeɯj pɐŋhjɐŋɯɫ ɡjʌndʑihɐjʌmɐtɐŋhi jetʃhɯkhɛjɐ hɐnɯn wʌntʃhiqe tɐɾɐ imi wɐnsudwen tɕebɐn tɕunbisɐʌpe dɛhɛ tɕʌnmjʌndʑʌqin ɡʌmsɐɾɯɫ tɕinhɛŋhɐjʌttɐ .|kss|ko
